In [1]:
! git clone https://github.com/sunone5/pyESN/

Cloning into 'pyESN'...
remote: Enumerating objects: 106, done.
remote: Total 106 (delta 0), reused 0 (delta 0), pack-reused 106
Receiving objects: 100% (106/106), 1.17 MiB | 3.40 MiB/s, done.
Resolving deltas: 100% (53/53), done.


In [2]:
! cp /kaggle/working/pyESN/testing.py .
! cp /kaggle/working/pyESN/freqgen.ipynb .
! cp /kaggle/working/pyESN/mackey_glass_t17.npy .
! cp /kaggle/working/pyESN/mackey.ipynb .
! cp /kaggle/working/pyESN/pyESN.py .

In [3]:
import os
for dirname, _, filenames in os.walk('/kaggle/working'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

/kaggle/working/pyESN.py
/kaggle/working/__notebook__.ipynb
/kaggle/working/submission.csv
/kaggle/working/freqgen.ipynb
/kaggle/working/testing.py
/kaggle/working/mackey.ipynb
/kaggle/working/mackey_glass_t17.npy
/kaggle/working/pyESN/pyESN.py
/kaggle/working/pyESN/freqgen.ipynb
/kaggle/working/pyESN/license.md
/kaggle/working/pyESN/testing.py
/kaggle/working/pyESN/mackey.ipynb
/kaggle/working/pyESN/mackey_glass_t17.npy
/kaggle/working/pyESN/readme.md
/kaggle/working/pyESN/.git/index
/kaggle/working/pyESN/.git/config
/kaggle/working/pyESN/.git/packed-refs
/kaggle/working/pyESN/.git/description
/kaggle/working/pyESN/.git/HEAD
/kaggle/working/pyESN/.git/logs/HEAD
/kaggle/working/pyESN/.git/logs/refs/heads/master
/kaggle/working/pyESN/.git/logs/refs/remotes/origin/HEAD
/kaggle/working/pyESN/.git/refs/heads/master
/kaggle/working/pyESN/.git/refs/remotes/origin/HEAD
/kaggle/working/pyESN/.git/hooks/fsmonitor-watchman.sample
/kaggle/working/pyESN/.git/hooks/post-update.sample
/kaggle/workin

In [4]:
import numpy as np 
import pandas as pd
import pandas_profiling

import matplotlib.pyplot as plt
import plotly.graph_objects as go
import seaborn as sns

from pyESN import ESN 

pd.set_option('max.columns', None)

from warnings import filterwarnings
filterwarnings('ignore')

import statsmodels.api as sm
from statsmodels.tsa.stattools import adfuller

In [5]:
stock_prices = pd.read_csv("../input/jpx-tokyo-stock-exchange-prediction/train_files/stock_prices.csv")
financials = pd.read_csv("../input/jpx-tokyo-stock-exchange-prediction/train_files/financials.csv")
options = pd.read_csv("../input/jpx-tokyo-stock-exchange-prediction/train_files/options.csv")
stock_list = pd.read_csv("../input/jpx-tokyo-stock-exchange-prediction/stock_list.csv")
trades = pd.read_csv('../input/jpx-tokyo-stock-exchange-prediction/train_files/trades.csv')
secondary_sp = pd.read_csv("../input/jpx-tokyo-stock-exchange-prediction/train_files/secondary_stock_prices.csv")
supplemental_sp = pd.read_csv("../input/jpx-tokyo-stock-exchange-prediction/supplemental_files/stock_prices.csv")
supplemental_ssp = pd.read_csv("../input/jpx-tokyo-stock-exchange-prediction/supplemental_files/secondary_stock_prices.csv")
test_prices = pd.read_csv("../input/jpx-tokyo-stock-exchange-prediction/example_test_files/sample_submission.csv")

In [6]:
datasets = [stock_prices,financials,options,stock_list,trades,secondary_sp,supplemental_sp,supplemental_ssp]

labels = ['stock_prices','financials','options','stock_list','trades','secondary_sp','supplemental_stock_prices','supplemental_secondary_stock_prices']

sizes = [len(i) for i in datasets]

plt.figure(figsize = (12,8))

sns.barplot(x = labels , y = sizes)

<AxesSubplot:>

In [7]:
tuple(zip(labels,sizes))

(('stock_prices', 2332531),
 ('financials', 92956),
 ('options', 3567694),
 ('stock_list', 4417),
 ('trades', 1712),
 ('secondary_sp', 2384575),
 ('supplemental_stock_prices', 195993),
 ('supplemental_secondary_stock_prices', 207042))

In [8]:
stock_prices_profile = stock_prices.profile_report(title='Pandas Profiling Report')
#stock_prices_profile.to_file(output_file="stock_prices_profiling.html")
stock_prices_profile

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [9]:
stock_prices.describe()

SecuritiesCode          Open          High           Low         Close  \
count    2.332531e+06  2.324923e+06  2.324923e+06  2.324923e+06  2.324923e+06   
mean     5.894835e+03  2.594511e+03  2.626540e+03  2.561227e+03  2.594023e+03   
std      2.404161e+03  3.577192e+03  3.619363e+03  3.533494e+03  3.576538e+03   
min      1.301000e+03  1.400000e+01  1.500000e+01  1.300000e+01  1.400000e+01   
25%      3.891000e+03  1.022000e+03  1.035000e+03  1.009000e+03  1.022000e+03   
50%      6.238000e+03  1.812000e+03  1.834000e+03  1.790000e+03  1.811000e+03   
75%      7.965000e+03  3.030000e+03  3.070000e+03  2.995000e+03  3.030000e+03   
max      9.997000e+03  1.099500e+05  1.105000e+05  1.072000e+05  1.095500e+05   

             Volume  AdjustmentFactor  ExpectedDividend        Target  
count  2.332531e+06      2.332531e+06      18865.000000  2.332293e+06  
mean   6.919366e+05      1.000508e+00         22.017730  4.450962e-04  
std    3.911256e+06      6.773040e-02         29.882453  2.339879e-02  
min    0.000000e+00      1.000000e-01          0.000000 -5.785414e-01  
25%    3.030000e+04      1.000000e+00          5.000000 -1.049869e-02  
50%    1.071000e+05      1.000000e+00         15.000000  0.000000e+00  
75%    4.021000e+05      1.000000e+00         30.000000  1.053159e-02  
max    6.436540e+08      2.000000e+01       1070.000000  1.119512e+00